## Import Data

In [1]:
# Setup Packages
import numpy as np
import pandas as pd
import math
import matplotlib.pyplot as plt

%matplotlib inline

# Display all rows and columns
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)

In [32]:
house_data = pd.read_csv('train.csv')
# house_data = pd.read_csv('test.csv')

remove_outlier = 1  # change to 0 for test data

<IPython.core.display.Javascript object>

## Data Manipulation

### Response Variable - Log Transform
- Transformation validated in DataExploration Notebook

In [33]:
house_data['SalePrice_log'] = np.log(house_data['SalePrice'])

<IPython.core.display.Javascript object>

### Impute Continuous Variables
- Imputation with mean validated in DataExploration Notebook

In [35]:
house_data["LotFrontage"].mean()

70.04995836802642

<IPython.core.display.Javascript object>

In [36]:
# LotFrontage
avg_LotFrontage = house_data['LotFrontage'].mean()
house_data['LotFrontage'].fillna(avg_LotFrontage, inplace=True)

# MasVnrArea
avg_LotFrontage = house_data['MasVnrArea'].mean()
house_data['MasVnrArea'].fillna(avg_LotFrontage, inplace=True)


<IPython.core.display.Javascript object>

### Impute Categorical Variables

In [5]:
#Impute NA values with 'None'
house_data['BsmtQual'].fillna('None', inplace=True)
house_data['BsmtCond'].fillna('None', inplace=True)
house_data['BsmtExposure'].fillna('None', inplace=True)
house_data['BsmtFinType1'].fillna('None', inplace=True)
train_data_cat_var.at[948,'BsmtExposure']='No'

<IPython.core.display.Javascript object>

In [6]:
#Electrical Fill with Mode
house_data['Electrical'].fillna(house_data['Electrical'].mode()[0], inplace=True)

<IPython.core.display.Javascript object>

In [7]:
#Fire Place Quality
house_data['FireplaceQu'].fillna('None', inplace=True)

<IPython.core.display.Javascript object>

In [9]:
#Garage Related Variables
house_data['GarageType'].fillna('None', inplace=True)
house_data['GarageFinish'].fillna('None', inplace=True)
house_data['GarageQual'].fillna('None', inplace=True)

<IPython.core.display.Javascript object>

In [ ]:
house_data['PoolQC'].fillna("None", inplace=True)

In [ ]:
house_data['Fence'].fillna("None", inplace=True)

In [ ]:
house_data['MiscFeature'].fillna("None", inplace=True)

## Feature Engineering

In [10]:
#Total area of house = Above ground living area + basement living area
house_data['TotalSF'] = house_data['GrLivArea'] + house_data['TotalBsmtSF']

<IPython.core.display.Javascript object>

In [11]:
#Age = Year sold - year built
house_data['Age'] = house_data['YrSold'] + house_data['YearBuilt']

<IPython.core.display.Javascript object>

In [12]:
#AgeRemod = Year sold - year remodeled
house_data['Age'] = house_data['YrSold'] + house_data['YearRemodAdd']

<IPython.core.display.Javascript object>

In [13]:
#Total porch SF = OpenPorchSF + EnclosedSF + 3SsnPorch + ScreenPorch
house_data['TotPorchSF'] = house_data['OpenPorchSF'] + house_data['EnclosedPorch'] + house_data['3SsnPorch'] + house_data['ScreenPorch']

<IPython.core.display.Javascript object>

In [14]:
#Total bathrooms = Full bath + 0.5*Halfbath (for both house and basement)
house_data['TotBaths'] = house_data['FullBath'] + house_data['BsmtFullBath'] + 0.5*house_data['HalfBath'] + 0.5*house_data['BsmtHalfBath']

<IPython.core.display.Javascript object>

In [15]:
#Total number of car garage = 1, 2, 3+ cars
house_data['TotCarGarage'] = pd.Series(len(house_data['GarageCars']), index=house_data.index)
house_data['TotCarGarage'] = 0 
house_data.loc[house_data['GarageCars'] >= 3,'TotCarGarage'] = 1

/Users/jonathanharris/opt/anaconda3/lib/python3.7/site-packages/pandas/core/indexing.py:205: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self._setitem_with_indexer(indexer, value)


<IPython.core.display.Javascript object>

In [16]:
#Has Second Floor = 0 (no) or 1 (yes)
house_data['Has2ndFl'] = pd.Series(len(house_data['2ndFlrSF']), index=house_data.index)
house_data['Has2ndFl'] = 0 
house_data.loc[house_data['2ndFlrSF'] > 0,'Has2ndFl'] = 1


<IPython.core.display.Javascript object>

In [18]:
#Has Porch = 0 (no) or 1 (yes)
house_data['HasPorch'] = pd.Series(len(house_data['TotPorchSF']), index=house_data.index)
house_data['HasPorch'] = 0 
house_data.loc[house_data['TotPorchSF'] > 0,'HasPorch'] = 1


<IPython.core.display.Javascript object>

In [19]:
#Has Deck = 0 (no) or 1 (yes)
house_data['HasDeck'] = pd.Series(len(house_data['WoodDeckSF']), index=house_data.index)
house_data['HasDeck'] = 0 
house_data.loc[house_data['WoodDeckSF'] > 0,'HasDeck'] = 1

<IPython.core.display.Javascript object>

In [20]:
#Has Pool = 0 (no) or 1 (yes)
house_data['HasPool'] = pd.Series(len(house_data['PoolArea']), index=house_data.index)
house_data['HasPool'] = 0 
house_data.loc[house_data['PoolArea'] > 0,'HasPool'] = 1

<IPython.core.display.Javascript object>

In [21]:
#Has Fireplace = 0 (no), 1 (yes, not excellent quality), or 2 (excellent quality)
house_data['HasFirePlace'] = pd.Series(len(house_data['FireplaceQu']), index=house_data.index)
house_data['HasFirePlace'] = 1 #default all houses have a fireplace 
house_data.loc[house_data['FireplaceQu'].isna(),'HasFirePlace'] = 0 #replace 1 with 0 for 'No Fireplace'
house_data.loc[house_data['FireplaceQu']== 'Ex','HasFirePlace'] = 2 #replace 1 with 2 for 'Excellent Fireplace'

<IPython.core.display.Javascript object>

In [22]:
#Has Gas Heating = 0 (no) or 1 (yes, GasA or GasW)
house_data['HasGasHeating'] = pd.Series(len(house_data['Heating']), index=house_data.index)
house_data['HasGasHeating'] = 0 
house_data.loc[house_data['Heating']== 'GasA','HasGasHeating'] = 1
house_data.loc[house_data['Heating']== 'GasW','HasGasHeating'] = 1

<IPython.core.display.Javascript object>

In [24]:
#Has Modern Circuitbreaker = 0 (no) or 1 (yes)
house_data['HasSBrkr'] = pd.Series(len(house_data['Electrical']), index=house_data.index)
house_data['HasSBrkr'] = 0 
house_data.loc[house_data['Electrical']== 'SBrkr','HasSBrkr'] = 1

<IPython.core.display.Javascript object>

In [25]:
#Has excellent basement quality = 0 (no) or 1 (yes)
house_data['HasExBsmtQual'] = pd.Series(len(house_data['BsmtQual']), index=house_data.index)
house_data['HasExBsmtQual'] = 0 
house_data.loc[house_data['BsmtQual']== 'Ex','HasExBsmtQual'] = 1

<IPython.core.display.Javascript object>

In [26]:
#Has Basement Exposure = 0 (no) or 1 (yes)
house_data['HasGd'] = pd.Series(len(house_data['BsmtExposure']), index=house_data.index)
house_data['HasGd'] = 0 
house_data.loc[house_data['BsmtExposure']== 'Gd','HasGd'] = 1

<IPython.core.display.Javascript object>

In [27]:
#Has Basement with good living quarters = 0 (no) or 1 (yes)
house_data['HasGLQ'] = pd.Series(len(house_data['BsmtFinType1']), index=house_data.index)
house_data['HasGLQ'] = 0 
house_data.loc[house_data['BsmtFinType1']== 'GLQ','HasGLQ'] = 1

<IPython.core.display.Javascript object>

In [28]:
#Has paved driveway = 0 (no) or 1 (yes)
house_data['HasPavedDrive'] = pd.Series(len(house_data['PavedDrive']), index=house_data.index)
house_data['HasPavedDrive'] = 0 
house_data.loc[house_data['PavedDrive']== 'Y','HasPavedDrive'] = 1

<IPython.core.display.Javascript object>

In [ ]:
house_data['HasTA'] = pd.Series(len(house_data['GarageQual']), index=house_data.index)
house_data['HasTA'] = 0 
house_data.loc[house_data['GarageQual']== 'TA','HasTA'] = 1

## Take stock of columns 

In [ ]:
# house_data has all of the columns
# cat_var_all is subset 
# drop_cat_var_all

In [2]:
cat_var_all= ['BsmtQual', 'BsmtCond', 'BsmtExposure', 'BsmtFinType1', 'BsmtFinType2', 'Heating', 'HeatingQC', 'CentralAir', 'Electrical',
              'KitchenQual', 'Functional', 'FireplaceQu', 'GarageType', 'GarageFinish', 'GarageQual', 'GarageCond', 'PavedDrive', 
              'PoolQC', 'Fence', 'MiscFeature','SaleType', 'SaleCondition', 'SalePrice_log', 'SalePrice']

drop_cat_var_all= ['Heating','Electrical', 'BsmtQual', 'BsmtExposure', 'BsmtFinType1', 'PavedDrive', 'GarageQual']
cat_only_drop=['Fence', 'MiscFeature', 'SaleType']
ordinal_drop=['BsmtFinType2','Functional', 'PoolQC', 'GarageCond', 'SaleCondition']




## One hot encode 

In [ ]:
'''
def Diff(li1, li2): 
    li_dif = [i for i in li1 + li2 if i not in li1 or i not in li2] 
    return li_dif 

train_data_cat_var_final= []
cols= Diff(list(train_data_cat_var_final.columns),['SalePrice_log', 'SalePrice'])

house_data_subset = pd.get_dummies(house_data[cols], prefix=cols, columns=cols, drop_first=True)

## Remove Outliers

In [30]:
# # Separate predictors by numerical and categorical features
# from functions_file import categorize

# cat_features, num_cont_features, num_disc_features = categorize(house_data)

# # Determine Outliers of Continuous Data
# def outlier_idx(data, thresh):

#     avg = data.mean()  # calc average
#     stdev = data.std()  # calc standard deviation
#     z_score = (data - avg) / stdev  # calc z_score
#     ol = z_score > thresh  # boolean (True=outlier)
#     outlier_idx = data.index[ol]  # indexes of outliers

#     return list(outlier_idx)


# # Plot Outliers
# plt.figure(figsize=(15, 20))
# for idx, col in enumerate(num_cont_features):
#     outliers = outlier_idx(house_data[col], 6)  # outlier indices
#     plt.subplot(math.ceil(len(num_cont_features) / ncol), ncol, idx + 1)
#     plt.scatter(x=house_data[col], y=house_data["SalePrice_log"], c="blue")
#     plt.scatter(
#         x=house_data[col][outliers], y=house_data["SalePrice_log"][outliers], c="red"
#     )
#     plt.ylabel("SalePrice_log")
#     plt.xlabel(col)

NameError: name 'plt' is not defined

<IPython.core.display.Javascript object>

In [ ]:
# vars_outliers = 'LotFrontage', 'LotArea', 'MasVnrArea', 'TotalBsmtSF', 'GrLivArea'

# outlier_store = {}
# thresh = 6  # outlier > +6std away from mean

# for idx, col in enumerate(num_cont_features):
#     outliers = outlier_idx(house_data[col], thresh)  # outlier indices

#     if len(outliers) > 0:
#         outlier_store[col] = outliers  # only store features with outliers

## Remove Variables

## Consolidate Data Feature Engineered: Train_test

In [42]:
house_data = pd.read_csv('csv')
house_data.shape
house_data2= pd.read_csv('train1_kc.csv')
house_data2.shap

(1460, 23)

In [136]:
jon_rich_test_feat= pd.read_csv('jon_rich_test_feature.csv')
kailun_test_feat= pd.read_csv('test1_kc.csv')

In [138]:
kailun_test_feat.head()

Unnamed: 0  HasGasHeating  HasSBrkr  HasEx  HasGd  HasGLQ  HasPavedDrive  \
0           0              1         1      0      0       0              1   
1           1              1         1      0      0       0              1   
2           2              1         1      0      0       1              1   
3           3              1         1      0      0       1              1   
4           4              1         1      0      0       0              1   

   HasTA  BsmtCond_Gd  BsmtCond_None  BsmtCond_Po  BsmtCond_TA  HeatingQC_Fa  \
0      1            0              0            0            1             0   
1      1            0              0            0            1             0   
2      1            0              0            0            1             0   
3      1            0              0            0            1             0   
4      1            0              0            0            1             0   

   HeatingQC_Gd  HeatingQC_Po  HeatingQC_TA  CentralAir_Y  KitchenQual_Fa  \
0             0             0             1             1               0   
1             0             0             1             1               0   
2             1             0             0             1               0   
3             0             0             0             1               0   
4             0             0             0             1               0   

   KitchenQual_Gd  KitchenQual_TA  FireplaceQu_Fa  FireplaceQu_Gd  \
0               0               1               0               0   
1               1               0               0               0   
2               0               1               0               0   
3               1               0               0               1   
4               1               0               0               0   

   FireplaceQu_None  FireplaceQu_Po  FireplaceQu_TA  GarageType_Attchd  \
0                 1               0               0                  1   
1                 1               0               0                  1   
2                 0               0               1                  1   
3                 0               0               0                  1   
4                 1               0               0                  1   

   GarageType_Basment  GarageType_BuiltIn  GarageType_CarPort  \
0                   0                   0                   0   
1                   0                   0                   0   
2                   0                   0                   0   
3                   0                   0                   0   
4                   0                   0                   0   

   GarageType_Detchd  GarageType_None  GarageFinish_None  GarageFinish_RFn  \
0                  0                0                  0                 0   
1                  0                0                  0                 0   
2                  0                0                  0                 0   
3                  0                0                  0                 0   
4                  0                0                  0                 1   

   GarageFinish_Unf  
0                 1  
1                 1  
2                 0  
3                 0  
4                 0

In [111]:
jon_rich_test_feat= jon_rich_test_feat.drop('Unnamed: 0', axis=1)
kailun_test_feat= kailun_test_feat.drop('Unnamed: 0', axis=1)

In [46]:
# This is only for training data 
Id= np.array(house_data['Id'])-1
house_data['Id']= Id
house_data= house_data.drop(['SalePrice', 'SalePrice_log'], axis=1)

In [53]:
train_all=pd.merge(house_data, house_data2, how= 'left', left_on= 'Id', right_on= house_data2.index)

In [139]:
test_feature=pd.merge(jon_rich_test_feat, kailun_test_feat, how= 'left', left_on= jon_rich_test_feat.index, right_on= kailun_test_feat.index)

In [43]:
house_data.columns

Index(['Unnamed: 0', 'Id', 'MSZoning', 'Street', 'Alley', 'LotShape',
       'LandContour', 'Utilities', 'LotConfig', 'LandSlope', 'Neighborhood',
       'Condition1', 'Condition2', 'BldgType', 'HouseStyle', 'RoofStyle',
       'RoofMatl', 'Exterior1st', 'Exterior2nd', 'MasVnrType', 'ExterQual',
       'ExterCond', 'Foundation'],
      dtype='object')

In [58]:
train_all=train_all.drop(['Unnamed: 0_y', 'Unnamed: 0_x'], axis=1)

In [62]:
test_feature.to_csv('train_all.csv')

In [134]:
test_feature= test_feature.drop('key_0', axis=1)

In [142]:
test_feature=test_feature.drop('key_0', axis=1)
test_feature.head()

Unnamed: 0_x    Id  MSSubClass  LotFrontage  LotArea  OverallQual  \
0             0  1461          20         80.0    11622            5   
1             1  1462          20         81.0    14267            6   
2             2  1463          60         74.0    13830            5   
3             3  1464          60         78.0     9978            6   
4             4  1465         120         43.0     5005            8   

   OverallCond  MasVnrArea  ExterQual  BsmtFinSF1  BsmtUnfSF  TotalBsmtSF  \
0            6         0.0          3         468        270          882   
1            6       108.0          3         923        406         1329   
2            5         0.0          3         791        137          928   
3            6        20.0          3         602        324          926   
4            5         0.0          4         263       1017         1280   

   1stFlrSF  GrLivArea  BedroomAbvGr  KitchenAbvGr  TotRmsAbvGrd  Fireplaces  \
0       896        896             2             1             5           0   
1      1329       1329             3             1             6           0   
2       928       1629             3             1             6           1   
3       926       1604             3             1             7           1   
4      1280       1280             2             1             5           0   

  GarageArea  GarageYrBlt  MoSold  WoodDeckSF  MiscVal  TotalSF  Age  \
0        730         1961       6         140        0     1778   49   
1        312         1958       6         393    12500     2658   52   
2        482         1997       3         212        0     2557   13   
3        470         1998       6         360        0     2530   12   
4        506         1992       1           0        0     2560   18   

   TotPorchSF  TotBaths  TotCarGarage  Has2ndFl  HasPorch  HasDeck  HasPool  \
0         120       1.0             0         0         1        1        0   
1          36       1.5             0         0         1        1        0   
2          34       2.5             0         1         1        1        0   
3          36       2.5             0         1         1        1        0   
4         226       2.0             0         0         1        0        0   

   HasIrregularLotShape  HasLandSlope  FoundationType  HasStoneMas  \
0                     0             0               1            0   
1                     1             0               1            0   
2                     1             0               2            0   
3                     1             0               2            0   
4                     1             0               2            0   

   NeighborhoodType  Unnamed: 0_y  HasGasHeating  HasSBrkr  HasEx  HasGd  \
0                 1             0              1         1      0      0   
1                 1             1              1         1      0      0   
2                 1             2              1         1      0      0   
3                 1             3              1         1      0      0   
4                 2             4              1         1      0      0   

   HasGLQ  HasPavedDrive  HasTA  BsmtCond_Gd  BsmtCond_None  BsmtCond_Po  \
0       0              1      1            0              0            0   
1       0              1      1            0              0            0   
2       1              1      1            0              0            0   
3       1              1      1            0              0            0   
4       0              1      1            0              0            0   

   BsmtCond_TA  HeatingQC_Fa  HeatingQC_Gd  HeatingQC_Po  HeatingQC_TA  \
0            1             0             0             0             1   
1            1             0             0             0             1   
2            1             0             1             0             0   
3            1             0             0             0             0   
4            

In [144]:
test_feature=test_feature.drop('Unnamed: 0_x', axis=1)
test_feature.head()
test_feature=test_feature.drop('Unnamed: 0_y', axis=1)
test_feature.head()

Id  MSSubClass  LotFrontage  LotArea  OverallQual  OverallCond  \
0  1461          20         80.0    11622            5            6   
1  1462          20         81.0    14267            6            6   
2  1463          60         74.0    13830            5            5   
3  1464          60         78.0     9978            6            6   
4  1465         120         43.0     5005            8            5   

   MasVnrArea  ExterQual  BsmtFinSF1  BsmtUnfSF  TotalBsmtSF  1stFlrSF  \
0         0.0          3         468        270          882       896   
1       108.0          3         923        406         1329      1329   
2         0.0          3         791        137          928       928   
3        20.0          3         602        324          926       926   
4         0.0          4         263       1017         1280      1280   

   GrLivArea  BedroomAbvGr  KitchenAbvGr  TotRmsAbvGrd  Fireplaces GarageArea  \
0        896             2             1             5           0        730   
1       1329             3             1             6           0        312   
2       1629             3             1             6           1        482   
3       1604             3             1             7           1        470   
4       1280             2             1             5           0        506   

   GarageYrBlt  MoSold  WoodDeckSF  MiscVal  TotalSF  Age  TotPorchSF  \
0         1961       6         140        0     1778   49         120   
1         1958       6         393    12500     2658   52          36   
2         1997       3         212        0     2557   13          34   
3         1998       6         360        0     2530   12          36   
4         1992       1           0        0     2560   18         226   

   TotBaths  TotCarGarage  Has2ndFl  HasPorch  HasDeck  HasPool  \
0       1.0             0         0         1        1        0   
1       1.5             0         0         1        1        0   
2       2.5             0         1         1        1        0   
3       2.5             0         1         1        1        0   
4       2.0             0         0         1        0        0   

   HasIrregularLotShape  HasLandSlope  FoundationType  HasStoneMas  \
0                     0             0               1            0   
1                     1             0               1            0   
2                     1             0               2            0   
3                     1             0               2            0   
4                     1             0               2            0   

   NeighborhoodType  HasGasHeating  HasSBrkr  HasEx  HasGd  HasGLQ  \
0                 1              1         1      0      0       0   
1                 1              1         1      0      0       0   
2                 1              1         1      0      0       1   
3                 1              1         1      0      0       1   
4                 2              1         1      0      0       0   

   HasPavedDrive  HasTA  BsmtCond_Gd  BsmtCond_None  BsmtCond_Po  BsmtCond_TA  \
0              1      1            0              0            0            1   
1              1      1            0              0            0            1   
2              1      1            0              0            0            1   
3              1      1            0              0            0            1   
4              1      1            0              0            0            1   

   HeatingQC_Fa  HeatingQC_Gd  HeatingQC_Po  HeatingQC_TA  CentralAir_Y  \
0             0             0             0             1             1   
1             0             0             0             1             1   
2             0             1             0             0             1   
3             0             0             0             0             1   
4             0             0             0             0             1   

   KitchenQual_Fa  Kitch

In [ ]:
cont_var_JH= ['Id','LotFrontage', 'LotArea', 'MasVnrArea', 'BsmtFinSF1', 'BsmtUnfSF', 'TotalBsmtSF',
'1stFlrSF', 'LowQualFinSF', 'GrLivArea', 'GarageYrBlt', 'GarageArea', 'WoodDeckSF',
'MiscVal','TotalSF', 'Age', 'TotPorchSF', 'TotBaths', 'MoSold', 'TotCarGarage']

cat_var_JH= ['Has2ndFl','NeighborhoodType','HasPorch', 'HasDeck', 'HasPool'] 

In [145]:
test_feature.to_csv('test_feature.csv')

## Consolidated DATA  Train_ Test 

In [45]:
jon= pd.read_csv('jon_original_HouseData.csv')
rich = pd.read_csv('rk_hotencode.csv')
kailun= pd.read_csv('train_all0.csv')

In [90]:
jon_test= pd.read_csv('jon_test_HouseData.csv')
rich_test = pd.read_csv('rk_hotencode_test.csv')
kailun_test= pd.read_csv('test_all0.csv')

In [122]:
# Examine Data 
kailun_test

Id  BsmtQual  BsmtCond  BsmtExposure  BsmtFinType1  BsmtFinType2  \
0        0         4         4             2             4             3   
1        1         4         4             2             6             2   
2        2         5         4             2             7             2   
3        3         4         4             2             7             2   
4        4         5         4             2             6             2   
5        5         5         4             2             2             2   
6        6         5         4             2             6             2   
7        7         5         4             2             2             2   
8        8         5         4             5             7             2   
9        9         4         4             2             6             4   
10      10         5         4             2             7             5   
11      11         4         4             2             4             2   
12      12         4         4             2             4             2   
13      13         4         4             2             6             2   
14      14         5         4             2             2             2   
15      15         6         4             2             2             2   
16      16         5         4             2             2             2   
17      17         6         4             2             7             2   
18      18         6         4             2             7             2   
19      19         6         4             5             7             2   
20      20         5         4             5             7             2   
21      21         5         4             3             7             2   
22      22         5         4             2             2             2   
23      23         5         4             4             7             2   
24      24         5         4             2             7             2   
25      25         5         4             2             2             2   
26      26         6         4             2             2             2   
27      27         5         4             2             2             2   
28      28         5         4             2             2             2   
29      29         6         4             2             7             2   
30      30         5         4             4             2             2   
31      31         4         4             2             2             2   
32      32         4         4             5             5             7   
33      33         5         4             2             3             7   
34      34         5         4             2             7             2   
35      35         6         4             4             7             2   
36      36         5         4             2             2             2   
37      37         5         4             4             7             2   
38      38         5         4             2             7             6   
39      39         5         4             2             7             2   
40      40         5         4             2             7             2   
41      41         5         4             2             7             2   
42      42         6         2             2             7             2   
43      43         5         4             2             7             2   
44      44         5         4             2             7             2   
45      45         4         4             2             7             2   
46      46         5         4             3             7             2   
47      47         5         4             3             6             3   
48      48         4         4             2             6             2   
49      49         4         4             2             4             2   
50      50         5         4             2             5             2   
51      51         4         4             2            

In [98]:
rich_test= rich_test.drop('Unnamed: 0', axis=1)
jon_test= jon_test.drop('Unnamed: 0', axis=1)

In [77]:
# Note this is not needed for Test data set since there are no outliers 
Id= np.array(jon['Id'])-1
jon['Id']= Id
#house_data= house_data.drop(['SalePrice', 'SalePrice_log'], axis=1)
jon= jon.drop(['Unnamed: 0'], axis=1)

In [63]:
train_all_cat=pd.merge(kailun, rich, how= 'left', left_on= 'Id', right_on= rich.index)

In [101]:
test_all_cat=pd.merge(jon_test, rich_test, how= 'left', left_on='Id', right_on= 'Id' )

In [65]:
drop=['Id_x', 'Id_y', 'Unnamed: 0', ]
train_all_cat= train_all_cat.drop('Unnamed: 0', axis=1)

In [79]:
train_all_final= pd.merge(jon, train_all_cat, how='left', left_on= 'Id', right_on= 'Id')

In [127]:
test_all_final=pd.merge(test_all_cat, kailun_test, how= 'left', left_on= test_all_cat.index, right_on= kailun_test.index)

In [86]:
drop=['SalePrice_x','SalePrice_log_x']
train_all_final=train_all_final.drop(drop, axis=1)

In [128]:
#test_all_final.head()
drop=[ 'Id_y', 'key_0' ]
test_all_final= test_all_final.drop(drop, axis=1)

In [ ]:
cat_var_RK= ['Alley','BldgType','Exterior1st', 'Condition1', 'Condition2', 'Exterior2nd', 'Foundation', 'HouseStyle', 
             'LandContour','LotConfig', 'MasVnrType', 'MSSubClass', 'MSZoning', 'RoofMatl', 'Street', 'Utilities']
ord_var_RK= ['ExterCond', 'ExterQual', 'LandSlope', 'LotShape']

In [ ]:
cat_var_KC= ['HasGasHeating', 'Electrical_combined', 'CentralAir_Y', 'GarageType_Combined', 
             'GarageQual_combined','HasPavedDrive', 'SaleType_combined', 'SalesCond_Combined']
ord_var_KC= ['BsmtQual', 'BsmtCond', 'BsmtExposure', 'BsmtFinType1', 'BsmtFinType2', 'HeatingQC',
            'KitchenQual', 'Functional', 'FireplaceQu', 'GarageFinish', 'GarageCond', 'Fence']

In [ ]:
cat_var_JH= ['MoSold','YrSold', 'GarageYrBlt']

In [88]:
train_all_final.to_csv('train_all_final.csv')

In [130]:
test_all_final.to_csv('test_all_final.csv')

In [129]:
test_all_final

Id_x  LotFrontage  LotArea  OverallQual  OverallCond  YearBuilt  \
0     1461    80.000000    11622            5            6       1961   
1     1462    81.000000    14267            6            6       1958   
2     1463    74.000000    13830            5            5       1997   
3     1464    78.000000     9978            6            6       1998   
4     1465    43.000000     5005            8            5       1992   
5     1466    75.000000    10000            6            5       1993   
6     1467    68.580357     7980            6            7       1992   
7     1468    63.000000     8402            6            5       1998   
8     1469    85.000000    10176            7            5       1990   
9     1470    70.000000     8400            4            5       1970   
10    1471    26.000000     5858            7            5       1999   
11    1472    21.000000     1680            6            5       1971   
12    1473    21.000000     1680            5            5       1971   
13    1474    24.000000     2280            6            6       1975   
14    1475    24.000000     2280            7            6       1975   
15    1476   102.000000    12858            9            5       2009   
16    1477    94.000000    12883            8            5       2009   
17    1478    90.000000    11520            9            5       2005   
18    1479    79.000000    14122            8            5       2005   
19    1480   110.000000    14300            9            5       2003   
20    1481   105.000000    13650            8            5       2002   
21    1482    41.000000     7132            8            5       2006   
22    1483   100.000000    18494            6            5       2005   
23    1484    43.000000     3203            7            5       2006   
24    1485    67.000000    13300            7            5       2004   
25    1486    63.000000     8577            7            5       2004   
26    1487    60.000000    17433            8            5       1998   
27    1488    73.000000     8987            8            5       2005   
28    1489    92.000000     9215            7            5       2009   
29    1490    84.000000    10440            6            5       2005   
30    1491    70.000000    11920            7            5       2004   
31    1492    70.000000     9800            5            5       1920   
32    1493    39.000000    15410            6            6       1974   
33    1494    85.000000    13143            8            5       1993   
34    1495    88.000000    11134            8            5       1992   
35    1496    25.000000     4835            7            5       2004   
36    1497    39.000000     3515            7            5       2004   
37    1498    30.000000     3215            7            5       2004   
38    1499    24.000000     2544            7            5       2004   
39    1500    24.000000     2544            6            5       2005   
40    1501    68.580357     2980            6            5       2000   
41    1502    68.580357     2403            7            5       2003   
42    1503    57.000000    12853            8            5       2010   
43    1504    68.000000     7379            8            5       2000   
44    1505    80.000000     8000            7            5       2002   
45    1506    68.580357    10456            6            6       1967   
46    1507    80.000000    10791            6            5       1993   
47    1508    68.580357    18837            6            5       1978   
48    1509    80.000000     9600            6            6       1971   
49    1510    80.000000     9600            5            5       1966   
50    1511    90.000000     9900            5            5       1966   
51    1512    88.000000     9680            5            6       1967   
52    1513    68.580357    10600            6            5       1964   
53    1514    98.000000    13260            5            6      